In [1]:
import pandas as pd
import nltk
# nltk.download('all')
import re
import numpy as np
import collections
import sklearn as sk
import string
from nltk.corpus import stopwords
from wordcloud import WordCloud, STOPWORDS
stopwords = set(STOPWORDS)

In [2]:
df = pd.read_csv("../B_Data_Cleaning/cleaned_real_reviews.csv")
df["Review"] = df["Review"].astype("str")
df

Review  \
0      day someone came ps version game quite journey...   
1               replay immediately demolish adam smasher   
2      patch fixed everything quests make sense fixer...   
3      watches edgerunners downloads cyberpunk time life   
4      remember hearing cyberpunk around announced in...   
...                                                  ...   
16594                                              boobs   
16595  great main story cyberpunk atmosphere good vis...   
16596                   got hardware run game definitely   
16597  glitches experience enough hold awesomeness ga...   
16598  frankly dont negative press game amazing right...   

       Recommended or Not Recommended  Date Timestamp Created  
0                                True              1645046263  
1                                True              1663224196  
2                                True              1645267750  
3                                True              1667117035  
4                                True              1664423074  
...                               ...                     ...  
16594                            True              1608792512  
16595                            True              1608792267  
16596                            True              1608777643  
16597                            True              1608777582  
16598                            True              1608770360  

[16599 rows x 3 columns]

In [3]:
# make a set_column to count the number of words in each review
df["set_column"] = df["Review"].apply(lambda x: set(x.split()))
df

Review  \
0      day someone came ps version game quite journey...   
1               replay immediately demolish adam smasher   
2      patch fixed everything quests make sense fixer...   
3      watches edgerunners downloads cyberpunk time life   
4      remember hearing cyberpunk around announced in...   
...                                                  ...   
16594                                              boobs   
16595  great main story cyberpunk atmosphere good vis...   
16596                   got hardware run game definitely   
16597  glitches experience enough hold awesomeness ga...   
16598  frankly dont negative press game amazing right...   

       Recommended or Not Recommended  Date Timestamp Created  \
0                                True              1645046263   
1                                True              1663224196   
2                                True              1645267750   
3                                True              1667117035   
4                                True              1664423074   
...                               ...                     ...   
16594                            True              1608792512   
16595                            True              1608792267   
16596                            True              1608777643   
16597                            True              1608777582   
16598                            True              1608770360   

                                              set_column  
0      {campaign, brought, actually, soft, weirdly, b...  
1         {replay, demolish, immediately, adam, smasher}  
2      {feels, actually, fixers, addiction, alive, bi...  
3      {edgerunners, cyberpunk, life, watches, time, ...  
4      {piece, watched, made, come, auto, sale, actua...  
...                                                  ...  
16594                                            {boobs}  
16595  {options, dialog, visuals, overall, cyberpunk,...  
16596             {hardware, got, run, game, definitely}  
16597  {awesomeness, thisll, enough, experience, game...  
16598  {significant, dont, game, anyway, playability,...  

[16599 rows x 4 columns]

In [4]:
# keep only 5250 reviews for each based on 'Recommended or Not Recommended" column
temp_recom = df.loc[df["Recommended or Not Recommended"] == True,:]
temp_recom = temp_recom.sample(5250).reset_index(drop=True)

temp_not_recom = df.loc[df["Recommended or Not Recommended"] == False,:]
temp_not_recom = temp_not_recom.sample(5250).reset_index(drop=True)

# combine temp_recom and temp_not_recom
temp = pd.concat([temp_recom, temp_not_recom], axis=0).reset_index(drop=True)

# split the data into train and test
train, test = sk.model_selection.train_test_split(temp, test_size=0.33, random_state=42)

# # split df_recom into train and test
# df_recom = temp_recom.sample(frac=0.67, random_state=42).reset_index(drop=True)
# test_recom = temp_recom.drop(df_recom.index).reset_index(drop=True)
# print(f"train size df_recom: {len(df_recom)}, test size df_recom: {len(test_recom)}")

# # split df_not_recom into train and test
# df_not_recom = temp_not_recom.sample(frac=0.33, random_state=42).reset_index(drop=True)
# test_not_recom = temp_not_recom.drop(df_not_recom.index).reset_index(drop=True)
# print(f"train size df_not_recom: {len(df_not_recom)}, test size df_not_recom: {len(test_not_recom)}")

# # combine test_recom and test_not_recom
# test = pd.concat([test_recom, test_not_recom], axis=0).reset_index(drop=True)

In [5]:
# Dividing dataset into recommended and not recommended
df_recom = train.loc[train["Recommended or Not Recommended"] == True,:]
df_recom = df_recom.reset_index(drop=True)

df_not_recom = train.loc[train["Recommended or Not Recommended"] == False,:]
df_not_recom = df_not_recom.reset_index(drop=True)

In [6]:
# This is to make the set dictionary
# count how many times each word appears in the reviews
bow_recom_temp = collections.Counter([y for x in df_recom.set_column for y in x])
bow_not_recom_temp = collections.Counter([y for x in df_not_recom.set_column for y in x])

bow_recom_set = dict(bow_recom_temp)
bow_not_recom_set = dict(bow_not_recom_temp)

for key in bow_recom_set:
    if key not in bow_not_recom_set:
        bow_not_recom_set[key] = 0
        pass
    else:
        pass

for key in bow_not_recom_set:
    if key not in bow_recom_set:
        bow_recom_set[key] = 0
        pass
    else:
        pass

for key in bow_recom_set:
    bow_recom_set[key] += 1

for key in bow_not_recom_set:
    bow_not_recom_set[key] += 1


In [7]:
# This is to make the list dictionary
# count how many times each word appears in the reviews
bow_recom = collections.Counter([y for x in df_recom.Review for y in x.split()])
bow_not_recom = collections.Counter([y for x in df_not_recom.Review for y in x.split()])

bow_recom_dict = dict(bow_recom)
bow_not_recom_dict = dict(bow_not_recom)

for key in bow_recom_dict:
    if key not in bow_not_recom_dict:
        bow_not_recom_dict[key] = 0
        pass
    else:
        pass

for key in bow_not_recom_dict:
    if key not in bow_recom_dict:
        bow_recom_dict[key] = 0
        pass
    else:
        pass

for key in bow_recom_dict:
    bow_recom_dict[key] += 1

for key in bow_not_recom_dict:
    bow_not_recom_dict[key] += 1
    

In [8]:
bow_recom_sum_vals = sum(bow_recom_dict.values())
bow_not_recom_sum_vals = sum(bow_not_recom_dict.values())

for i in bow_recom_dict:

    bow_recom_dict[i] /= bow_recom_sum_vals

for i in bow_not_recom_dict:

    bow_not_recom_dict[i] /= bow_not_recom_sum_vals

In [9]:
assert len(bow_recom_dict) == len(bow_not_recom_dict)
assert len(bow_recom_set) == len(bow_not_recom_set)

In [10]:
test.drop(columns=["set_column"], inplace=True)

In [11]:
def define_sentiment_all(element,test1=False, test2=False):

    """This function takes a review and returns the label for that review"""

    full_shape = df.shape[0]
    positive_review_probabiliy = len(df_recom)/full_shape
    negative_review_probabiliy = len(df_not_recom)/full_shape
    
    df_choices_positive = [positive_review_probabiliy, bow_recom_set, bow_recom_dict, df_recom]
    df_choices_negative = [negative_review_probabiliy ,bow_not_recom_set, bow_not_recom_dict, df_not_recom]

    def classifier(element, your_class = 'positive'):
        flag = {}
        flag_count = 0
        if your_class == 'positive':
            df_choices = df_choices_positive
        else:
            df_choices = df_choices_negative
        prob_of_class = df_choices[0]/full_shape
        score = 1 * prob_of_class
        score = float(format(score, '.12f'))
        # score = 0.1
        for i in element.split():
            if i not in df_choices[2].keys():
                pass
            else:
                prob_word_given_class = (df_choices[2])[i]
                prob_word_given_class = float(format(prob_word_given_class, '.12f'))
                # Almost the same value, given our spin on this application. 
                # Normally, this term frequency would be calculated differently across the positive and negative documents
                # but we are only looking at the reviews as the documents themselves to determine a word's relevance in the positive
                # or negative corpus. 
                tf = np.log(prob_word_given_class)
                # tf = float(format(tf, '.12f'))
                # tf = abs(np.log(prob_word_given_class))
                # The IDF is the number of reviews / the number of reviews that contain the word in that given corpus
                # idf = abs(np.log(df_choices[3].shape[0]/(df_choices[1])[i]))
                idf = np.log(df_choices[3].shape[0]/(df_choices[1])[i])
                # idf = float(format(idf, '.12f'))
                score *= prob_word_given_class*tf*idf
                # score *= prob_word_given_class*idf
                # score *= prob_word_given_class*tf
                # score *= prob_word_given_class

                if score < 0:
                    flag[flag_count] = (score, your_class)
                    print(flag_count,i)
                    flag_count += 1


        return score
    positive_score = classifier(element, 'positive')
    negative_score = classifier(element, 'negative')
    if positive_score > negative_score:
        return True
    elif positive_score == negative_score:
        # Choosing an arbitrary value, because we assume that a review with one or few words of little substance
        # is implied to be negative, as is usual with netizens. 
        return False
    else:
        return False

In [12]:
def define_sentiment_idf(element,test1=False, test2=False):

    """This function takes a review and returns the label for that review"""

    full_shape = df.shape[0]
    positive_review_probabiliy = len(df_recom)/full_shape
    negative_review_probabiliy = len(df_not_recom)/full_shape
    
    df_choices_positive = [positive_review_probabiliy, bow_recom_set, bow_recom_dict, df_recom]
    df_choices_negative = [negative_review_probabiliy ,bow_not_recom_set, bow_not_recom_dict, df_not_recom]

    def classifier(element, your_class = 'positive'):
        flag = {}
        flag_count = 0
        if your_class == 'positive':
            df_choices = df_choices_positive
        else:
            df_choices = df_choices_negative
        prob_of_class = df_choices[0]/full_shape
        score = 1 * prob_of_class
        score = float(format(score, '.12f'))
        # score = 0.1
        for i in element.split():
            if i not in df_choices[2].keys():
                pass
            else:
                prob_word_given_class = (df_choices[2])[i]
                prob_word_given_class = float(format(prob_word_given_class, '.12f'))
                # Almost the same value, given our spin on this application. 
                # Normally, this term frequency would be calculated differently across the positive and negative documents
                # but we are only looking at the reviews as the documents themselves to determine a word's relevance in the positive
                # or negative corpus. 
                tf = np.log(prob_word_given_class)
                # tf = float(format(tf, '.12f'))
                # tf = abs(np.log(prob_word_given_class))
                # The IDF is the number of reviews / the number of reviews that contain the word in that given corpus
                # idf = abs(np.log(df_choices[3].shape[0]/(df_choices[1])[i]))
                idf = np.log(df_choices[3].shape[0]/(df_choices[1])[i])
                # idf = float(format(idf, '.12f'))
                # score *= prob_word_given_class*tf*idf
                score *= prob_word_given_class*idf
                # score *= prob_word_given_class*tf
                # score *= prob_word_given_class

                if score < 0:
                    flag[flag_count] = (score, your_class)
                    print(flag_count,i)
                    flag_count += 1


        return score
    positive_score = classifier(element, 'positive')
    negative_score = classifier(element, 'negative')
    if positive_score > negative_score:
        return True
    elif positive_score == negative_score:
        # Choosing an arbitrary value, because we assume that a review with one or few words of little substance
        # is implied to be negative, as is usual with netizens. 
        return False
    else:
        return False

In [13]:
def define_sentiment_tf(element,test1=False, test2=False):

    """This function takes a review and returns the label for that review"""

    full_shape = df.shape[0]
    positive_review_probabiliy = len(df_recom)/full_shape
    negative_review_probabiliy = len(df_not_recom)/full_shape
    
    df_choices_positive = [positive_review_probabiliy, bow_recom_set, bow_recom_dict, df_recom]
    df_choices_negative = [negative_review_probabiliy ,bow_not_recom_set, bow_not_recom_dict, df_not_recom]

    def classifier(element, your_class = 'positive'):
        flag = {}
        flag_count = 0
        if your_class == 'positive':
            df_choices = df_choices_positive
        else:
            df_choices = df_choices_negative
        prob_of_class = df_choices[0]/full_shape
        score = 1 * prob_of_class
        score = float(format(score, '.12f'))
        # score = 0.1
        for i in element.split():
            if i not in df_choices[2].keys():
                pass
            else:
                prob_word_given_class = (df_choices[2])[i]
                prob_word_given_class = float(format(prob_word_given_class, '.12f'))
                # Almost the same value, given our spin on this application. 
                # Normally, this term frequency would be calculated differently across the positive and negative documents
                # but we are only looking at the reviews as the documents themselves to determine a word's relevance in the positive
                # or negative corpus. 
                tf = np.log(prob_word_given_class)
                # tf = float(format(tf, '.12f'))
                # tf = abs(np.log(prob_word_given_class))
                # The IDF is the number of reviews / the number of reviews that contain the word in that given corpus
                # idf = abs(np.log(df_choices[3].shape[0]/(df_choices[1])[i]))
                idf = np.log(df_choices[3].shape[0]/(df_choices[1])[i])
                # idf = float(format(idf, '.12f'))
                # score *= prob_word_given_class*tf*idf
                # score *= prob_word_given_class*idf
                score *= prob_word_given_class*tf
                # score *= prob_word_given_class

                if score < 0:
                    flag[flag_count] = (score, your_class)
                    print(flag_count,i)
                    flag_count += 1


        return score
    positive_score = classifier(element, 'positive')
    negative_score = classifier(element, 'negative')
    if positive_score > negative_score:
        return True
    elif positive_score == negative_score:
        # Choosing an arbitrary value, because we assume that a review with one or few words of little substance
        # is implied to be negative, as is usual with netizens. 
        return False
    else:
        return False

In [14]:
def define_sentiment_freq(element,test1=False, test2=False):

    """This function takes a review and returns the label for that review"""

    full_shape = df.shape[0]
    positive_review_probabiliy = len(df_recom)/full_shape
    negative_review_probabiliy = len(df_not_recom)/full_shape
    
    df_choices_positive = [positive_review_probabiliy, bow_recom_set, bow_recom_dict, df_recom]
    df_choices_negative = [negative_review_probabiliy ,bow_not_recom_set, bow_not_recom_dict, df_not_recom]

    def classifier(element, your_class = 'positive'):
        flag = {}
        flag_count = 0
        if your_class == 'positive':
            df_choices = df_choices_positive
        else:
            df_choices = df_choices_negative
        prob_of_class = df_choices[0]/full_shape
        score = 1 * prob_of_class
        score = float(format(score, '.12f'))
        # score = 0.1
        for i in element.split():
            if i not in df_choices[2].keys():
                pass
            else:
                prob_word_given_class = (df_choices[2])[i]
                prob_word_given_class = float(format(prob_word_given_class, '.12f'))
                # Almost the same value, given our spin on this application. 
                # Normally, this term frequency would be calculated differently across the positive and negative documents
                # but we are only looking at the reviews as the documents themselves to determine a word's relevance in the positive
                # or negative corpus. 
                tf = np.log(prob_word_given_class)
                # tf = float(format(tf, '.12f'))
                # tf = abs(np.log(prob_word_given_class))
                # The IDF is the number of reviews / the number of reviews that contain the word in that given corpus
                # idf = abs(np.log(df_choices[3].shape[0]/(df_choices[1])[i]))
                idf = np.log(df_choices[3].shape[0]/(df_choices[1])[i])
                # idf = float(format(idf, '.12f'))
                # score *= prob_word_given_class*tf*idf
                # score *= prob_word_given_class*idf
                # score *= prob_word_given_class*tf
                score *= prob_word_given_class

                if score < 0:
                    flag[flag_count] = (score, your_class)
                    print(flag_count,i)
                    flag_count += 1


        return score
    positive_score = classifier(element, 'positive')
    negative_score = classifier(element, 'negative')
    if positive_score > negative_score:
        return True
    elif positive_score == negative_score:
        # Choosing an arbitrary value, because we assume that a review with one or few words of little substance
        # is implied to be negative, as is usual with netizens. 
        return False
    else:
        return False

In [15]:
test["score_all"] = test.Review.apply(define_sentiment_all)
test["score_tf"] = test.Review.apply(define_sentiment_tf)
test["score_idf"] = test.Review.apply(define_sentiment_idf)
test["score_freq"] = test.Review.apply(define_sentiment_freq)

0 expected
0 expected
0 latest
1 cyberscam
2 broken
3 basic
4 functioning
5 intelligence
6 promises
7 games
8 time
9 game
10 held
11 duct
12 glue
13 will
14 moment
15 use
16 titles
17 inferior
18 way
19 customization
20 locations
21 content
22 functioning
23 world
24 physics
25 hitboxes
26 devoid
27 promises
28 content
29 demos
30 wrong
31 potential
32 right
33 running
34 breaking
35 breaking
36 start
37 devoid
38 mechanics
39 game
40 favor
41 game
42 now
43 buggy
44 trash
45 will
46 responsible
47 final
48 update
49 release
50 game
51 hot
52 update
53 new
54 havent
55 done
56 salt
57 cdpr
58 weak
59 dlc
60 car
61 johnny
62 cdpr
63 come
64 update
65 months
66 nothing
67 buggy
68 state
69 still
70 still
71 continues
72 will
73 devs
74 upcoming
75 holding
76 will
77 fix
0 latest
1 cyberscam
2 broken
3 basic
4 functioning
5 intelligence
6 promises
7 games
8 time
9 game
10 held
11 duct
12 glue
13 will
14 moment
15 use
16 titles
17 inferior
18 way
19 customization
20 locations
21 content
22

In [16]:
print(f"This is our accuracy for (balanced) real data when we use all the formula: {(sum(test['Recommended or Not Recommended'] == test['score_all'])/test.shape[0])*100:.2f}%")
print(f"This is our accuracy for (balanced) real data when we use only frequency and TF: {(sum(test['Recommended or Not Recommended'] == test['score_tf'])/test.shape[0])*100:.2f}%")
print(f"This is our accuracy for (balanced) real data when we use only frequency and IDF: {(sum(test['Recommended or Not Recommended'] == test['score_idf'])/test.shape[0])*100:.2f}%")
print(f"This is our accuracy for (balanced) real data when we use only frequency: {(sum(test['Recommended or Not Recommended'] == test['score_freq'])/test.shape[0])*100:.2f}%")

This is our accuracy for (balanced) real data when we use all the formula: 51.14%
This is our accuracy for (balanced) real data when we use only frequency and TF: 51.08%
This is our accuracy for (balanced) real data when we use only frequency and IDF: 69.93%
This is our accuracy for (balanced) real data when we use only frequency: 75.73%


In [17]:
# Generate a confusion matrix
from sklearn.metrics import confusion_matrix
confusion_matrix(test['Recommended or Not Recommended'], test['score_all'])
# Generate a classification report
from sklearn.metrics import classification_report
print(classification_report(test['Recommended or Not Recommended'], test['score_all']))


              precision    recall  f1-score   support

       False       0.50      0.59      0.54      1699
        True       0.52      0.43      0.48      1766

    accuracy                           0.51      3465
   macro avg       0.51      0.51      0.51      3465
weighted avg       0.51      0.51      0.51      3465



In [18]:
# Generate a confusion matrix
from sklearn.metrics import confusion_matrix
confusion_matrix(test['Recommended or Not Recommended'], test['score_tf'])
# Generate a classification report
from sklearn.metrics import classification_report
print(classification_report(test['Recommended or Not Recommended'], test['score_tf']))


              precision    recall  f1-score   support

       False       0.50      0.59      0.54      1699
        True       0.52      0.43      0.47      1766

    accuracy                           0.51      3465
   macro avg       0.51      0.51      0.51      3465
weighted avg       0.51      0.51      0.51      3465



In [19]:
# Generate a confusion matrix
from sklearn.metrics import confusion_matrix
confusion_matrix(test['Recommended or Not Recommended'], test['score_idf'])
# Generate a classification report
from sklearn.metrics import classification_report
print(classification_report(test['Recommended or Not Recommended'], test['score_idf']))


              precision    recall  f1-score   support

       False       0.73      0.61      0.67      1699
        True       0.68      0.79      0.73      1766

    accuracy                           0.70      3465
   macro avg       0.70      0.70      0.70      3465
weighted avg       0.70      0.70      0.70      3465



In [20]:
# Generate a confusion matrix
from sklearn.metrics import confusion_matrix
confusion_matrix(test['Recommended or Not Recommended'], test['score_freq'])
# Generate a classification report
from sklearn.metrics import classification_report
print(classification_report(test['Recommended or Not Recommended'], test['score_freq']))


              precision    recall  f1-score   support

       False       0.71      0.86      0.78      1699
        True       0.83      0.66      0.74      1766

    accuracy                           0.76      3465
   macro avg       0.77      0.76      0.76      3465
weighted avg       0.77      0.76      0.76      3465

